In [ ]:
import pandas as pd
import numpy as np 
import glob
import os 

In [ ]:
# Caminho onde estão as subpastas com os arquivos CSV

# Set the path to the folder containing CSV files
folder_path = r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\DRAFT_HISTÓRICO DE VENDAS_MAR"  # arquivo dos drafts

# Pattern to match all CSV files
csv_files = glob.glob(os.path.join(folder_path, '*.csv'))

# Read and concat all CSVs
df_draft = pd.concat([pd.read_csv(file) for file in csv_files], ignore_index=True)

df_draft['match'] = 1 

df_draft.shape


In [ ]:
df_draft.columns

In [ ]:
#df_draft = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\DRAFT_HISTÓRICO DE VENDAS_MAR\pegou em excel\DRAFT_PDVS_SEM_23701-20992_20250423090756.xlsx",sheet_name='BOTICARIO')


#df_draft['match'] = 1 

#df_draft.shape

In [ ]:
df_draft = df_draft.drop(columns='Quantidade')


In [ ]:


# Caminho onde estão as subpastas com os arquivos CSV
pasta_entrada = r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\ESTOQUE_ATUAL"

# Lista todas as subpastas dentro de "ESTOQUE"
subpastas = [os.path.join(pasta_entrada, d) for d in os.listdir(pasta_entrada) if os.path.isdir(os.path.join(pasta_entrada, d))]

df_list = []

# Percorre todas as subpastas
for subpasta in subpastas:
    arquivos = [f for f in os.listdir(subpasta) if f.endswith(".csv")]
    nome_pasta = os.path.basename(subpasta)  # Obtém o nome da pasta

    for arquivo in arquivos:
        caminho_arquivo = os.path.join(subpasta, arquivo)
        try:
            df = pd.read_csv(caminho_arquivo, encoding="utf-8", low_memory=False)  # Melhor para grandes volumes de dados
            df["Arquivo_Origem"] = arquivo  # Adiciona o nome do arquivo de origem
            df["Pasta_Origem"] = nome_pasta  # Adiciona o nome da pasta de origem
            df_list.append(df)
        except Exception as e:
            print(f"Erro ao ler o arquivo {arquivo}: {e}")

if df_list:
    df_estoque = pd.concat(df_list, ignore_index=True)

df_estoque['PDV'] = df_estoque['PDV'].astype(str)

df_estoque['SKU_FINAL'] = np.where(df_estoque['SKU_PARA'] == "-", df_estoque['SKU'], df_estoque['SKU_PARA'])

df_estoque['SKU_FINAL']=df_estoque['SKU_FINAL'].astype(str)

df_estoque = df_estoque[df_estoque['Arquivo_Origem']== "BOT.csv"]


In [ ]:
df_bi_vendas = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\VENDAS BI\data (1).xlsx")

df_bi_vendas['Ciclo_ultimos2'] = df_bi_vendas['Ciclo'].str.rsplit('.', n=1).str[-1]

df_bi_vendas['Ciclo_ano'] = df_bi_vendas['Ciclo'].str.rsplit('.', n=1).str[0]

df_bi_vendas['Ciclo_ano'] = df_bi_vendas['Ciclo_ano'].str.replace("C","")

df_bi_vendas['CICLO_FINAL'] = 'C20' + df_bi_vendas['Ciclo_ano'].astype(str) + df_bi_vendas['Ciclo_ultimos2'].astype(str)



In [ ]:
df_bi_vendas.columns

In [ ]:
df_pdv = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\PDV\PDV_ATT.xlsx")

df_pdv_origi = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\PDV\PDV_ATT.xlsx")

df_pdv = df_pdv.rename(columns={'DESCRIÇÃO':'DESCRIÇÃO PDV'})

df_pdv = df_pdv.drop(columns=['REGIÃO', 'ESTADO','CIDADE','GESTÃO', 'status'])

df_pdv['PDV'] = df_pdv['PDV DESC'].str.split("-").str[0].str.strip()

df_pdv['UF'] = np.where(df_pdv['UF'] == 'VDC','BA',df_pdv['UF'])

#ignorando a PDV que ainda não está online
df_pdv = df_pdv[df_pdv['DESCRIÇÃO PDV'] != '23813-COMERCIO-HIB VALENTE']

df_pdv = df_pdv[df_pdv['SUPERVISOR'] != "Inativa"]

In [ ]:
df_pdv['PDV'] = df_pdv['PDV'].fillna(0).astype('int64')

In [ ]:
calendario = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\CICLO 9\CALENDARIO_CICLO\Ciclo_Expandido_com_Datas.xlsx")

calendario['Date'] = pd.to_datetime(calendario['Date'])

# Get today (normalized to midnight)
today = pd.Timestamp("today").normalize()

calendario['NUM_CICLO'] = calendario['Ciclo'].str[-2:].astype(int)

calendario['ANO_CICLO'] = calendario['Ciclo'].str[0:5]

calendario = calendario[calendario['MARCA'] == "BOTICARIO"]

calendario['CICLOMAIS2'] = calendario['ANO_CICLO'].astype(str) + (calendario['NUM_CICLO'].astype(int) + 3).astype(str).str.zfill(2)       #<<< MUDAR O "4" (CICLO ATUAL + 4 PARA ACHAR O CICLO DA SUGESTÃO) EX: C202505 -> C202509
ciclo_mais2 = calendario[calendario['Date'].dt.normalize() == today]['CICLOMAIS2'].iloc[0]

# Filter rows where date matches today
filtered_calendario = calendario[calendario['Ciclo'] == ciclo_mais2][:1]

filtered_calendario['dias_ate_inicio'] = filtered_calendario['INICIO CICLO'].iloc[0] - today

filtered_calendario['dias_ate_inicio'] = filtered_calendario['dias_ate_inicio'].dt.days.astype(int)

filtered_calendario['match'] = 1


In [ ]:
filtered_calendario

In [ ]:
df_tabela = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\TABELA_PEDIDO\Pedidos Semanais Especiais - BOT - 202510 (2).xlsx")

df_tabela = df_tabela[df_tabela['Região'] == 'NNE'] 

df_tabela = df_tabela[(df_tabela['Canal'] != 'Ecomm') | (df_tabela['Canal'] != 'Ecomm | VD') | (df_tabela['Canal'] != 'Ecomm | Loja')] #perguntar se isso aqui é vdd

df_tabela['Canal'] = np.where((df_tabela['Canal'] == "Loja") | (df_tabela['Canal'] == "Todos") | (df_tabela['Canal'] == "Loja | VD"),"TODOS","VD")

df_tabela = df_tabela[df_tabela['Tipo de promoção'].str.contains('Lançamentos', na=False)]

In [ ]:
df_tabela['Tipo de promoção'].value_counts()

In [ ]:
df_similares = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\PRODUTO_SIMILAR\PRODUTOS SIMILARES.xlsx")

In [ ]:
df_similares = pd.merge(left=df_similares,right=calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO']], how= 'left', left_on = 'CICLO SIMILAR',right_on = 'Ciclo' )

df_similares = df_similares.drop(columns=['INICIO DO CICLO SIMILAR','FIM DO CICLO SIMILAR', 'DURAÇÃO DO CICLO DO SIMILAR','Ciclo','DESCRIÇÃO SIMILAR'])

df_similares = df_similares.rename(columns={'INICIO CICLO':'INICIO CICLO SIMILAR','FIM CICLO':'FIM CICLO SIMILAR','DURAÇÃO':'DURAÇÃO CICLO SIMILAR'})
df_similares.drop_duplicates(inplace=True)

In [ ]:
df_draft = df_draft.rename(columns={'Descrição':'DESCRIÇÃO SIMILAR'})

df_draft = df_draft.drop(columns=['Subcategoria', 'Lançamento', 'Desativação',
                                   'Dias sem venda',
                                   'Promoção Próximo Ciclo', 'Promoção Próximo Ciclo + 1','Compra inteligente semanal/Sugestão de compra',
                                    'Compra inteligente Próximo Ciclo',
                                    'Compra inteligente Próximo Ciclo + 1', 'Item Desativado',
                                    'Data Prevista Regularização', 'Carteira Bloqueada Para Novos Pedidos',
                                    'Planograma', 'Quantidade por caixa', 'Preço Sell In','Item analisado', 'Histórico de Vendas do Ciclo 202505'])



In [ ]:
df_draft['PROJEÇÃO DE VENDAS CICLO'] =  df_draft['Projeção Próximo Ciclo + 1'] - df_draft['Projeção Próximo Ciclo']

In [ ]:
df_venda_diaria = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\VENDAS_PRATICO\VENDAS SIMI C10 - FormFiltroConsultaVendaSintetica_09_05_2025_11_30_54.xls")

df_venda_diaria.shape

In [ ]:
df_venda_diaria['PDV'] = df_venda_diaria['Unidade de Negócio'].str.split("-").str[0].str.strip()

df_venda_diaria['Dia'] = pd.to_datetime(df_venda_diaria['Dia'], format='%d/%m/%Y')

df_venda_diaria = pd.merge(left=df_venda_diaria,right=calendario[['Ciclo','Date']],left_on='Dia',right_on='Date',how='inner')

df_venda_diaria = df_venda_diaria.drop(columns='Date')

df_venda_diaria.shape

In [ ]:
df_venda_diaria = df_venda_diaria.drop_duplicates()

df_venda_diaria.shape

In [ ]:
df_venda_agrupado = df_venda_diaria.groupby(['PDV', 'Código do Produto','Ciclo'])['Quantidade'].sum().reset_index()
df_venda_agrupado

In [ ]:
df_pdv['MATCH'] = 1

df_similares['MATCH'] = 1

df_similares = pd.merge(left=df_similares,right=df_pdv,right_on=['MATCH'],left_on=['MATCH'],how='inner')

df_similares = df_similares.drop_duplicates()

In [ ]:
df_similares.columns

In [ ]:
df_final = pd.merge(left=df_similares,right=df_draft,right_on=['SKU','PDV'],left_on=['PRODUTO SIMILAR','PDV'],how='left')
df_final.shape

In [ ]:
df_final = pd.merge(left=df_final, right=filtered_calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO','match','dias_ate_inicio']], on='match',how='left')
df_final.shape

In [ ]:


#df_final = pd.merge(left=df_final,right=df_pdv[['PDV', 'CANAL', 'DESCRIÇÃO PDV', 'PDV DESC','UF','ANALISTA','SUPERVISOR']],on = 'PDV',how='inner')
df_final.shape

In [ ]:
df_bi_vendas = df_bi_vendas.rename(columns={'Quantidade':'Vendas Ciclo Lançamento'})

In [ ]:

df_bi_vendas['SKU2'] = df_bi_vendas['SKU2'].astype(str) 

df_final['PRODUTO SIMILAR'] = df_final['PRODUTO SIMILAR'].astype(str)

df_bi_vendas['PDV'] = df_bi_vendas['PDV'].astype('Int64') 

df_final['SKU'] = df_final['SKU'].astype(str)

df_final = pd.merge(left=df_final,right=df_bi_vendas,right_on=['PDV','SKU2','CICLO_FINAL'],left_on=['PDV','PRODUTO SIMILAR','CICLO SIMILAR'],how='left')
df_final.shape   

In [ ]:
df_final.columns

In [ ]:
df_final = df_final.drop(columns=['SKU','match',
       'Ciclo_y',
       'SKU1', 'SKU2', 'Campanha','TOTAL PV',
       'Ciclo_ultimos2', 'Ciclo_ano', 'CICLO_FINAL'])

In [ ]:
df_final['CANAL'] = np.where((df_final['CANAL'] == 'LJ') | (df_final['CANAL'] == 'HIB'), "TODOS" , np.where((df_final['CANAL'] == 'CD') | (df_final['CANAL'] == 'VD'), "VD", df_final['CANAL']))

df_final['CANAL'].value_counts()

In [ ]:
df_tabela['Código'] = df_tabela['Código'].astype(str)
df_final['PRODUTO LANÇAMENTO'] = df_final['PRODUTO LANÇAMENTO'].astype(str)

df_final = pd.merge(left=df_final,right=df_tabela[['Canal', 'Código','Ação consumidor','IAF','Foco','Marca','Categoria',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor','Tipo de promoção']],right_on=['Código'],left_on=['PRODUTO LANÇAMENTO'],how='left')
df_final.shape  

In [ ]:
df_estoque = df_estoque.rename(columns={'SKU_FINAL':'SKU_PARA_VALIDACAO'})

In [ ]:
df_estoque['PDV'] = df_estoque['PDV'].astype('int64')

df_final = pd.merge( left= df_final, right = df_estoque[['SKU_PARA_VALIDACAO','Arquivo_Origem','PDV']], left_on= ['PRODUTO SIMILAR','PDV'], right_on=['SKU_PARA_VALIDACAO','PDV'], how='left')

In [ ]:
df_final = df_final.drop(columns=[
'SKU_PARA_VALIDACAO'])

In [ ]:
df_final.columns

In [ ]:
df_final.columns[35:41]

In [ ]:
df_final['PDV_SKU'] = df_final['PDV'].astype(str) + df_final['PRODUTO SIMILAR'].astype(str) 

df_final['UFPRODUTO'] = df_final['UF'].astype(str) + df_final['PRODUTO SIMILAR'].astype(str)


VENDA_SIMILAR_6_MESES= df_final.columns[35:41]

df_final['Pico Vendas Similar Ultimos 6 ciclos'] = df_final[VENDA_SIMILAR_6_MESES].max(axis=1)

df_final = df_final.drop_duplicates()



In [ ]:
df_venda_agrupado['PDV'] = df_venda_agrupado['PDV'].astype('int64')

df_final['CICLO SIMILAR'] = df_final['CICLO SIMILAR'].astype(str)

df_venda_agrupado['Código do Produto'] = df_venda_agrupado['Código do Produto'].astype(str)

df_final = pd.merge(left=df_final,right=df_venda_agrupado,right_on=['PDV','Código do Produto','Ciclo'],left_on=['PDV','PRODUTO SIMILAR','CICLO SIMILAR'],how='left')

In [ ]:
df_final = df_final.drop(columns=['Ciclo','Código do Produto','Vendas Ciclo Lançamento'])

df_final = df_final.rename(columns={'Quantidade':'Vendas Ciclo Lançamento'})

In [ ]:
df_final.columns[25:41]

In [ ]:
# Suponha que os meses estão nas colunas 10 a 26 (17 colunas = 17 meses)
colunas_mensais = df_final.columns[25:41]

# Passo 1: Soma todas as linhas (itens) por mês → resultado: total por mês
soma_mensal = df_final[colunas_mensais].sum()

# Passo 2: Calcula a variação percentual de um mês para o outro
variacao_mensal = soma_mensal.pct_change()
variacao_mensal = variacao_mensal.dropna()

variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

# Passo 3: Calcula a média da variação (ignorando o primeiro NaN)
media_variacao = variacao_mensal[1:].mean()

# Calcula média e desvio padrão
media = variacao_mensal.mean()
desvio = variacao_mensal.std()

# Define limite (ex: 2 desvios padrão)
limite_superior = media + 2 * desvio
limite_inferior = media - 2 * desvio

# Filtra dados dentro do limite
filtro = variacao_mensal.between(limite_inferior, limite_superior)
df_filtrado = variacao_mensal[filtro]
CRESCIMENTO = round(df_filtrado.mean(),4)

df_final['CRESCIMENTO'] = CRESCIMENTO

CRESCIMENTO


In [ ]:
variacao_mensal.info

In [ ]:
df_final.columns[27:28]

In [ ]:
venda_similar_mesmo_ciclo_ano_passado = df_final.columns[27:28] #<<<<<<< CICLO ATUAL É  [37:38]
ciclo_ano_passado = df_final.columns[27:28].str.split(" ")[0][-1]
df_final[ciclo_ano_passado] = df_final[venda_similar_mesmo_ciclo_ano_passado]

In [ ]:
df_final['Vendas Ciclo Lançamento'] = df_final['Vendas Ciclo Lançamento'].fillna(0)

In [ ]:
vendas_todos_historicos = df_final.columns[25:41]

df_final['MEDIANA DO HISTÓRICO'] = df_final[vendas_todos_historicos].dropna().median(axis=1)

df_final['MEDIA DO HISTÓRICO'] = df_final[vendas_todos_historicos].dropna().mean(axis=1)

df_final['MEDIANA DO HISTÓRICO'] = np.where(df_final['MEDIANA DO HISTÓRICO'] > 0, df_final['MEDIANA DO HISTÓRICO'], df_final['MEDIA DO HISTÓRICO'] )#validar se foi



In [ ]:
crescimento = df_final['CRESCIMENTO']
vendas_lanc = df_final['Vendas Ciclo Lançamento']
pico_similar = df_final['Pico Vendas Similar Ultimos 6 ciclos']
mediana_hist = df_final['MEDIANA DO HISTÓRICO']

# Primeiro cálculo intermediário
df_final['PV GINSENG'] = np.where(df_final['CRESCIMENTO'] * df_final[ciclo_ano_passado] + df_final[ciclo_ano_passado] < df_final['MEDIANA DO HISTÓRICO'],
                                    round(df_final['CRESCIMENTO'] * df_final['MEDIANA DO HISTÓRICO']+ df_final['MEDIANA DO HISTÓRICO'],0), 
                                    round(df_final['CRESCIMENTO']*df_final[ciclo_ano_passado]+df_final[ciclo_ano_passado],0))

In [ ]:
df_final.columns[25:38]

In [ ]:
df_final = df_final.rename(columns={df_final.columns[38]: "C-4", df_final.columns[39]: "C-3",df_final.columns[40]: "C-2",df_final.columns[41]: "C-1"})

df_final.drop(columns=df_final.columns[25:38], inplace=True)


In [ ]:
df_final.columns

In [ ]:

marca_promo =  df_estoque['Arquivo_Origem'].iloc[0].replace('.csv','')

df_final['INICIO CICLO'] = pd.to_datetime(df_final['INICIO CICLO'], dayfirst=True).dt.strftime('%d/%m/%Y')

df_final['FIM CICLO'] = pd.to_datetime(df_final['FIM CICLO'], dayfirst=True).dt.strftime('%d/%m/%Y')

df_final['INICIO CICLO SIMILAR'] = pd.to_datetime(df_final['INICIO CICLO SIMILAR'], dayfirst=True).dt.strftime('%d/%m/%Y')

df_final['FIM CICLO SIMILAR'] = pd.to_datetime(df_final['FIM CICLO SIMILAR'], dayfirst=True).dt.strftime('%d/%m/%Y')



df_final = df_final.rename(columns={'Ciclo_x': 'Ciclo'})

In [ ]:
df_final = pd.merge(left=df_final,right=df_pdv_origi[['PDV','CANAL','UF']],how='inner',on='PDV')

In [ ]:
df_final = df_final.drop(columns=['CANAL_x','UF_x','Categoria_y'])

df_final = df_final.rename(columns={'CANAL_y':'CANAL', 'UF_y':'UF','MARCA_x':'MARCA','Categoria_x':'Categoria'})

In [ ]:
# Columns to bring up front
priority_cols = [
    'Ciclo','INICIO CICLO','FIM CICLO','ANALISTA','SUPERVISOR','UF','CANAL','PDV', 'DESCRIÇÃO PDV','DURAÇÃO',	
    'Classe','PRODUTO LANÇAMENTO','DESCRIÇÃO DO LANÇAMENTO','MARCA','Foco',
    'PRODUTO SIMILAR','DESCRIÇÃO SIMILAR','CICLO SIMILAR','INICIO CICLO SIMILAR','FIM CICLO SIMILAR','DURAÇÃO CICLO SIMILAR',
    'Ação consumidor',	'Percentual de desconto consumidor','Ação revendedor','Percentual de desconto revendedor','Estoque Atual',
    'Estoque em Transito',	'Pedido Pendente','DESCRIÇÃO SIMILAR', 'Histórico de Vendas do Ciclo Atual',
	'C-4',	'C-3',	'C-2',	'C-1'
]

# All remaining columns
other_cols = [col for col in df_final.columns if col not in priority_cols]

# Reorder
df_final = df_final[priority_cols + other_cols]

df_final['SUGESTÃO ABTASTECIMENTO'] = ''

df_final['SUGESTÃO COMERCIAL'] = ''


In [ ]:
df_final = df_final.drop(columns=['Marca','CRESCIMENTO','Canal','Código','Tipo de promoção','dias_ate_inicio','PDV DESC','UFPRODUTO','Arquivo_Origem','UFPRODUTO',
                                  'PDV_SKU','MEDIANA DO HISTÓRICO','MEDIA DO HISTÓRICO'])

In [ ]:
df_final['chave'] = df_final['PDV'].astype(str) + df_final['PRODUTO LANÇAMENTO'].astype(str)

chaves_duplicadas = (
    df_final.groupby('chave')['Percentual de desconto consumidor']
    .count()
    .loc[lambda x: x == 2]
    .index
)

# Selecionar essas linhas
duplicadas = df_final[df_final['chave'].isin(chaves_duplicadas)]

# Filtrar apenas os grupos onde pelo menos uma linha tem 0.0
grupos_com_zero = duplicadas.groupby('chave').filter(
    lambda g: (g['Percentual de desconto consumidor'] == "0,00").any()
)

# Remover apenas as linhas com 0.0 dessas chaves
limpos = grupos_com_zero[grupos_com_zero['Percentual de desconto consumidor'] != "0,00"]

# Concatenar com o restante do dataframe que não foi afetado
resto = df_final[~df_final['chave'].isin(grupos_com_zero['chave'])]
df_final = pd.concat([resto, limpos], ignore_index=True)


In [ ]:

from openpyxl import load_workbook
from openpyxl.styles import PatternFill, Font


# Export to Excel
output_file = f'C:\\Users\\joao.herculano\\Documents\\Lançamento!!!_{marca_promo}_{ciclo_mais2}_20.05!!.xlsx'
with pd.ExcelWriter(output_file, engine='openpyxl') as writer:
    df_final.to_excel(writer, index=False, sheet_name='Sheet1')

# Apply styles
wb = load_workbook(output_file)
ws = wb['Sheet1']

# Style header
header_fill = PatternFill(start_color='ADD8E6', end_color='ADD8E6', fill_type='solid')  # Light Blue
header_font = Font(color='FFFFFF', bold=True)  # White & Bold

for cell in ws[1]:
    cell.fill = header_fill
    cell.font = header_font

# Style rows: gray/white alternating
gray_fill = PatternFill(start_color='DDDDDD', end_color='DDDDDD', fill_type='solid')  # Light gray

for i, row in enumerate(ws.iter_rows(min_row=2, max_row=ws.max_row), start=2):
    if i % 2 == 0:
        for cell in row:
            cell.fill = gray_fill

# Save styled workbook
wb.save(output_file)
